In [ ]:
# Copyright 2023 Google LLC
#
# Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
#     https://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

# Delta files from Google Cloud Storage

<table align="left">

<a href="https://github.com/GoogleCloudPlatform/ai-ml-recipes/blob/main/notebooks/foundational/delta_format/delta_quickstart.ipynb">
<img src="https://cloud.google.com/ml-engine/images/github-logo-32px.png" alt="GitHub logo">
View on GitHub
</a>
</td>
<td>
<a href="https://console.cloud.google.com/vertex-ai/workbench/deploy-notebook?download_url=https://raw.githubusercontent.com/GoogleCloudPlatform/ai-ml-recipes/main/notebooks/foundational/delta_format/delta_quickstart.ipynb">
<img src="https://lh3.googleusercontent.com/UiNooY4LUgW_oTvpsNhPpQzsstV5W8F7rYgxgGBD85cWJoLmrOzhVs_ksK_vgx40SHs7jCqkTkCk=e14-rj-sc0xffffff-h130-w32" alt="Vertex AI logo">
Open in Vertex AI Workbench
</a>
</td>
</table>

In this quickstart, you'll learn how to seamlessly interact with data stored in the Delta Lake format on Google Cloud Storage (GCS).  
We'll leverage the power of Dataproc Serverless runtimes, configured with the necessary Delta Lake libraries, to perform common data operations.  

When creating a Dataproc Runtime Template using the Dataproc Jupyterlab Plugin, setup the following Spark property:

**spark.jars**  
gs://dataproc-metastore-public-binaries/dependencies/delta-storage-3.1.0.jar,gs://dataproc-metastore-public-binaries/dependencies/delta-spark_2.13-3.1.0.jar

<center><img src="../../docs/images/delta-jars.png" width="50%" height="50%"/></center>


In [ ]:
from pyspark.sql import SparkSession

In [ ]:
spark = SparkSession.builder \
  .appName("delta") \
  .config("spark.sql.extensions", "io.delta.sql.DeltaSparkSessionExtension") \
  .config("spark.sql.catalog.spark_catalog", "org.apache.spark.sql.delta.catalog.DeltaCatalog") \
  .enableHiveSupport() \
  .getOrCreate()

#### You can read a dataset in the delta format from our public datasets

In [ ]:
df = spark.read.format("delta").option("header",True).load("gs://dataproc-metastore-public-binaries/gas_sensors")

In [ ]:
df.show()

| Times| COppm|Humidityrh|TemperatureC|FlowratemLmin|HeatervoltageV| R1MOhm| R2MOhm| R3MOhm| R4MOhm| R5MOhm| R6MOhm| R7MOhm| R8MOhm|R9MOhm|R10MOhm|R11MOhm|R12MOhm|R13MOhm|R14MOhm|
|------|------|----------|------------|-------------|--------------|-------|-------|-------|-------|-------|-------|-------|-------|------|-------|-------|-------|-------|-------|
|0.0000|0.0000|   32.7023|      9.9032|     240.8069|        0.8900| 0.0738| 0.1314| 0.0987| 0.0936| 0.1026| 0.1152| 0.1105| 0.0891|0.0951| 0.1083| 0.1037| 0.1009| 0.0927| 0.1009|
|0.3070|0.0000|   45.5699|     13.7998|     240.8029|        0.8950| 0.0786| 0.1286| 0.1019| 0.0932| 0.1051| 0.1129| 0.1128| 0.0905|0.0958| 0.1103| 0.1043| 0.1025| 0.0942| 0.1020|
|0.6170|0.0000|   58.5539|     17.7318|     240.7989|        0.8979| 0.0816| 0.1287| 0.1052| 0.0940| 0.1075| 0.1128| 0.1149| 0.0918|0.0966| 0.1119| 0.1050| 0.1036| 0.0958| 0.1028|
|0.9240|0.0000|   71.4123|     21.6256|     240.7949|        0.8971| 0.0834| 0.1303| 0.1083| 0.0954| 0.1100| 0.1138| 0.1172| 0.0928|0.0972| 0.1130| 0.1054| 0.1044| 0.0968| 0.1033|
|1.2340|0.0000|   83.8100|     25.3800|     240.7917|        0.8980| 0.0851| 0.1324| 0.1112| 0.0967| 0.1120| 0.1151| 0.1194| 0.0936|0.0976| 0.1138| 0.1057| 0.1049| 0.0975| 0.1038|
|1.5410|0.0000|   83.8100|     25.3800|     240.8061|        0.8986| 0.0867| 0.1343| 0.1138| 0.0981| 0.1139| 0.1165| 0.1213| 0.0942|0.0980| 0.1144| 0.1058| 0.1053| 0.0980| 0.1041|

#### You can write transformed data to your bucket in the delta format like this:

df.write.mode("append").format("delta").save("gs://\<YOUR_GCS_BUCKET\>/\<PATH\>/")